# Load data

In [1]:
import os
import numpy as np
import matplotlib.pyplot as plt
from glob import glob

import pandas as pd
import scipy.io as sio
import hdf5storage
import mne
import pickle

from mne.preprocessing import ICA
from scipy.signal.windows import hann

In [2]:
foldPaths = '../Recording_info.csv'
data_dir = '../data'
save_dir = '../Processed_data'

In [ ]:
# 檢查阻抗測試是否在實驗中間進行
def inter_impedance_inspect(trigger,onset,duration):

    if 'Start Impedance' in trigger:
        pos = np.where((trigger == 'Start Impedance') | (trigger == 'Stop Impedance'))[0]
        # Make sure that there is no impedance before the whole experiment
        trigger_left = trigger[int(pos[0]):]
        trigger_left = np.delete(trigger_left, [0,1])
        print(trigger_left)

        if trigger_left.size == 0:
            trigger = np.delete(trigger, pos)
            onset = np.delete(onset, pos)
            duration = np.delete(duration, pos)
            print("There is an Impedance in the dataset but at the end")

        else:
            print('A impedance occurs in the middle of the data')
            print(trigger)
            raise ValueError('Please Delete This Subject')
        
    return trigger, onset, duration

# 檢查觸發事件並識別實驗類型
def trigger_check(trigger,onset,duration):

    trigger_cate = list(set(list(trigger)))
    experiment = 1
    for trigg in [91,92,93,94,95,96]:
        if trigg in trigger_cate:
            experiment = 'ERP'

    if experiment == 'ERP':
        print("There is other dataset inside the data")

        real_Exper = np.where(trigger==100)[0][4]
        real_Exper_end = np.where(trigger==102)[0][-1]+1

        if real_Exper_end > real_Exper:
            pass

        else:
            real_Exper = np.where(trigger == 100)[0][3]

        trigger = trigger[real_Exper:real_Exper_end]
        onset = onset[real_Exper:real_Exper_end]
        duration = duration[real_Exper:real_Exper_end]

    return trigger, onset, duration

# 讀取 BDF 格式的 EEG 數據和事件
def read_data(folderPath, unit, sfreq):

    rawdata = mne.io.read_raw_bdf(os.path.join(folderPath, 'data.bdf'), preload=True)

    # Unit alignment -> V -> uV
    if unit == 'V':
        rawdata._data = rawdata._data * 1e6

    try:
        events = mne.read_annotations(os.path.join(folderPath, 'evt.bdf'))
        onset = np.array([int(x * sfreq) for x in events.onset] )
        duration = np.array([int(x) for x in events.duration])
        trigger = np.array([i for i in events.description])
        print("Original trigger events:", trigger)
        
        # Impedance checking
        trigger,onset,duration = inter_impedance_inspect(trigger,onset,duration)
        trigger = np.array([int(x) for x in trigger])
        
        # Check wheter there is ERP data
        trigger,onset, duration = trigger_check(trigger,onset, duration)
        return trigger, onset, duration, rawdata
    
    except:
        raise RuntimeError("No event was found")


# 將 EEG 數據按影片片段拼接
def data_concat(eegData, videoData: np.ndarray, video: int):
    fs = 250
    secs = 30  # fs * secs = 250 × 30 = 7500 个數据點（對應30秒的EEG數據）

    if len(videoData.shape) > 2:
        videoData = np.squeeze(videoData)

    trigger = np.zeros((1,fs * secs))
    trigger[0][0] = video
    
    print('The shape of current epoch:', videoData.shape)

    if videoData.shape[1] > fs * secs:
        videoData = videoData[:,-fs*secs:] #保留最后30秒

    elif videoData.shape[1] < fs * secs:
        raise RuntimeError("The length of epoch is wrong")
    
    videoData = np.vstack((videoData, trigger)) #將影片data直接嵌入數據，方便影片分類

    if eegData is None:
        eegData = videoData

    else:
        eegData = np.hstack((eegData, videoData))

    return eegData

# 將處理後的 EEG 數據保存為 pickle 文件
def eeg_save(subject:str, eegData_trigger: np.ndarray, filepath):

    if len(subject) == 1:
        subject = '00' + subject

    elif len(subject) == 2:
        subject = '0' + subject
    
    os.makedirs(filepath, exist_ok=True)
    f = open(filepath + '/' + subject +'.pkl','wb')
    pickle.dump(eegData_trigger, f)
    f.close()

# 調整通道順序以匹配標準 10-20 系統
def channel_modify(data, first_or_second):
    # data (33,210000)
    # 17, 16 's 參考電極
    new_order = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29,
                 30, 31, 17, 16, 32]
    
    # batch == 1
    if first_or_second == 1 :
        data = data[np.array(new_order),:]
        
    chns = 32 
    fs = 250
    n_vids = 28
    sec = 30
    eegdata = np.zeros((n_vids, chns, fs * sec))

    video_index = np.where(data[-1, :].T>0)[0]
    video_arange = np.argsort(data[-1, video_index])
    video_arange_index = video_index[video_arange]
    
    for idx, vid in enumerate(video_arange_index):
        eegdata[idx, :, :] = data[:-1, vid:vid + fs*sec]
    return eegdata

In [4]:
class Preprocessing:

    def __init__(self, raw: mne.epochs.Epochs):

        self.nchns = raw.info['nchan']

        self.freq = raw.info['sfreq']
        old_chn_names = raw.info['ch_names']
        new_chn_names = raw.info['ch_names'].copy()
        if 'A1' not in new_chn_names:
            new_chn_names[-2] = 'A2'
            new_chn_names[-1] = 'A1'

        chan_names_dict = {old_chn_names[i]: new_chn_names[i] for i in range(32)}
        raw.rename_channels(chan_names_dict)

        montage = mne.channels.make_standard_montage('standard_1020')
        raw.set_montage(montage)

        self.montage_index = dict(zip(np.arange(self.nchns) , new_chn_names))
        self.raw = raw
        self.data = self.raw.get_data()


    def band_pass_filter(self,l_freq,h_freq):
        self.raw.filter(l_freq,h_freq)

    def down_sample(self,n_freq):
        self.raw.resample(n_freq)

    # Should cut the data into pieces than do the interpolation
    def bad_channels_interpolate(self,thresh1=None, proportion=0.3):
        
        data = self.data 
        data = np.squeeze(data)
        Bad_chns = []
        value = 0
        
        md = np.median(np.abs(data))

        value = np.where(np.abs(data) > (thresh1 * md), 1, 0)[0]

        Bad_chns = np.argwhere((np.mean(value, axis=0) > proportion))
        
        if Bad_chns.size > 0:
            self.raw.info['bads'].extend([self.montage_index[str(bad)] for bad in Bad_chns] )
            print('Bad channels: ',self.raw.info['bads'])
            self.raw = self.raw.interpolate_bads()

        else:
            print('No bad channel currently')

    def eeg_ica(self):

        ica = ICA()
        ica.fit(self.raw)

        # 用ICA去除眼動雜訊
        eog_indices1, _ = ica.find_bads_eog(self.raw, ch_name='Fp1')
        eog_indices2, _ = ica.find_bads_eog(self.raw, ch_name='Fp2')
        
        eog_indices = list(set(eog_indices1 + eog_indices2))
        ica.exclude = eog_indices

        ica.apply(self.raw)

    def average_ref(self):
        # 將原始 EEG 轉成以詮腦平均為參考，降低参考電極噪音影響
        self.raw.set_eeg_reference(ref_channels='average')


In [5]:
pd_data = pd.read_csv(foldPaths,low_memory=False)
print(pd_data.keys())
sub_info = pd_data['sub']
sub_cohort = pd_data['Cohort']
sub_unit = pd_data['Unit']
sub_sfreq = pd_data['Sample_rate']
print(sub_info)
# print(sub_sfreq)

Index(['sub', 'Gender', 'Age', 'Cohort', 'Sample_rate', 'Unit'], dtype='object')
0      sub000
1      sub001
2      sub002
3      sub003
4      sub004
        ...  
118    sub118
119    sub119
120    sub120
121    sub121
122    sub122
Name: sub, Length: 123, dtype: object


In [6]:
import warnings
warnings.filterwarnings("ignore")

# 1 Read the data
for idx, sub in enumerate(sub_info):
    sub_path = os.path.join(data_dir,sub)
    frequency = sub_sfreq[idx]

    print("Current processing subject:", sub)
    trigger, onset, duration, rawdata = read_data(sub_path, sub_unit[idx], frequency)

    remark_data = hdf5storage.loadmat(os.path.join(sub_path, 'After_remarks.mat'))['After_remark']
    
    # vids = np.squeeze(remark_data['vid'])
    vids = remark_data['vid'].flatten()

    events = np.vstack((np.vstack((onset, duration)), trigger)).T

    # 根據實驗標記截取每个trial的EEG數據前30秒
    original_raw = rawdata.copy()

    cut_seconds = -30
    event_id = 102
    epochs = mne.Epochs(original_raw, events, event_id=event_id, tmin=cut_seconds, tmax=0, preload=True)

    video_trigger_index = np.where((trigger!=0)&(trigger<29))[0]

    eeg_Data_saved = None

    for index, pos in enumerate(video_trigger_index):

        video = trigger[pos]

        processed_epoch_ = Preprocessing(epochs[index])

        processed_epoch_.down_sample(250)
        
        processed_epoch_.band_pass_filter(0.05, 47)

        processed_epoch_.bad_channels_interpolate(thresh1=3, proportion=0.3)

        processed_epoch_.eeg_ica()

        processed_epoch_.average_ref()

        eeg_Data_saved = data_concat(eeg_Data_saved, processed_epoch_.raw.get_data(), video)

    video_index = np.where(eeg_Data_saved[-1,:].T>0)[0]
    if int(sub_cohort[idx]==1):
        cohort = 1
        eeg_Data_saved = channel_modify(eeg_Data_saved, cohort)
    elif int(sub_cohort[idx]==2):
        cohort = 2
        eeg_Data_saved = channel_modify(eeg_Data_saved, cohort)

    # Saved as pkl
    eeg_save(sub, eeg_Data_saved, save_dir)


Current processing subject: sub000
Extracting EDF parameters from c:\Users\User\Desktop\四下\腦機\final\finally\data\sub000\data.bdf...
BDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 4880999  =      0.000 ...  4880.999 secs...
Original trigger events: ['100' '100' '100' '100' '100' '11' '101' '102' '8' '101' '102' '2' '101'
 '102' '5' '101' '102' '6' '101' '102' '9' '101' '102' '3' '101' '102'
 '12' '101' '102' '20' '101' '102' '17' '101' '102' '26' '101' '102' '23'
 '101' '102' '13' '101' '102' '15' '101' '102' '14' '101' '102' '16' '101'
 '102' '10' '101' '102' '1' '101' '102' '4' '101' '102' '7' '101' '102'
 '28' '101' '102' '25' '101' '102' '22' '101' '102' '19' '101' '102' '18'
 '101' '102' '21' '101' '102' '27' '101' '102' '24' '101' '102'
 'Start Impedance' 'Stop Impedance']
[]
There is an Impedance in the dataset but at the end
Not setting metadata
28 matching events found
Setting baseline interval to [-30.0, 0.0] s
Applying baselin

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s
[Parallel(n_jobs=1)]: Done  32 out of  32 | elapsed:    0.0s finished


Fitting ICA to data using 32 channels (please be patient, this may take a while)
Selecting by non-zero PCA components: 32 components
Fitting ICA took 1.4s.
Using EOG channel: Fp1
Using EOG channel: Fp2
Applying ICA to Epochs instance
    Transforming to ICA space (32 components)
    Zeroing out 1 ICA component
    Projecting back using 32 PCA components
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
The shape of current epoch: (32, 7500)
Setting up band-pass filter from 0.05 - 47 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.05
- Lower transition bandwidth: 0.05 Hz (-6 dB cutoff frequency: 0.03 Hz)
- Upper passband edge: 47.00 Hz
- Upper transition bandwidth: 11.75 Hz (-6 dB cutoff frequency: 52.88 Hz)
- Filter leng

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s
[Parallel(n_jobs=1)]: Done  32 out of  32 | elapsed:    0.0s finished


Fitting ICA took 0.3s.
Using EOG channel: Fp1
Using EOG channel: Fp2
Applying ICA to Epochs instance
    Transforming to ICA space (31 components)
    Zeroing out 0 ICA components
    Projecting back using 32 PCA components
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
The shape of current epoch: (32, 7500)
Setting up band-pass filter from 0.05 - 47 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.05
- Lower transition bandwidth: 0.05 Hz (-6 dB cutoff frequency: 0.03 Hz)
- Upper passband edge: 47.00 Hz
- Upper transition bandwidth: 11.75 Hz (-6 dB cutoff frequency: 52.88 Hz)
- Filter length: 16501 samples (66.004 s)

No bad channel currently
Fitting ICA to data using 32 channels (please be patient, this may take a whi

...

Fitting ICA took 0.3s.
Using EOG channel: Fp1
Using EOG channel: Fp2
Applying ICA to Epochs instance
    Transforming to ICA space (32 components)
    Zeroing out 0 ICA components
    Projecting back using 32 PCA components
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
The shape of current epoch: (32, 7500)
Setting up band-pass filter from 0.05 - 47 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.05
- Lower transition bandwidth: 0.05 Hz (-6 dB cutoff frequency: 0.03 Hz)
- Upper passband edge: 47.00 Hz
- Upper transition bandwidth: 11.75 Hz (-6 dB cutoff frequency: 52.88 Hz)
- Filter length: 16501 samples (66.004 s)

No bad channel currently
Fitting ICA to data using 32 channels (please be patient, this may take a whi

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s
[Parallel(n_jobs=1)]: Done  32 out of  32 | elapsed:    0.0s finished


Fitting ICA took 0.3s.
Using EOG channel: Fp1
Using EOG channel: Fp2
Applying ICA to Epochs instance
    Transforming to ICA space (32 components)
    Zeroing out 1 ICA component
    Projecting back using 32 PCA components
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
The shape of current epoch: (32, 7500)
Setting up band-pass filter from 0.05 - 47 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.05
- Lower transition bandwidth: 0.05 Hz (-6 dB cutoff frequency: 0.03 Hz)
- Upper passband edge: 47.00 Hz
- Upper transition bandwidth: 11.75 Hz (-6 dB cutoff frequency: 52.88 Hz)
- Filter length: 16501 samples (66.004 s)

No bad channel currently
Fitting ICA to data using 32 channels (please be patient, this may take a whil

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s
[Parallel(n_jobs=1)]: Done  32 out of  32 | elapsed:    0.0s finished


Fitting ICA took 0.3s.
Using EOG channel: Fp1
Using EOG channel: Fp2
Applying ICA to Epochs instance
    Transforming to ICA space (32 components)
    Zeroing out 0 ICA components
    Projecting back using 32 PCA components
EEG channel type selected for re-referencing
Applying average reference.
Applying a custom ('EEG',) reference.
The shape of current epoch: (32, 7500)
